In [1]:
import numpy as np
import pandas as pd
import torch
import tensorly as tl


from tensorly.decomposition import parafac
from tensorly.decomposition import tucker
from tensorly.decomposition import tensor_train
from tensorly.decomposition import tensor_train
# different forms of tensor
from sklearn.preprocessing import MinMaxScaler
from tensorly import tt_to_tensor
from tensorly.decomposition import matrix_product_state
# tensor operations


#from math import ceil
#from google.colab import drive
#drive.mount('/content/gdrive')

import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.autograd import Variable
import torch.optim as optim
import torchvision
from torchvision import datasets, models, transforms, utils
from torch.utils.data import Dataset, DataLoader
import time
import os
import copy
import torch.nn.functional as Fun
print("PyTorch Version:", torch.__version__)
print("Torchvision Version:", torchvision.__version__)
print("GPU is available?", torch.cuda.is_available())

PyTorch Version: 1.13.1
Torchvision Version: 0.14.1
GPU is available? True


In [2]:
dtype = torch.float64
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

In [3]:
features = list()
with open("/home/c/cl237/TenBCD/UCI HAR/data/features.txt") as f:
    features = [line.split()[1] for line in f.readlines()]
print('# of Features: {}'.format(len(features)))

# of Features: 561


## get train data

In [4]:
pd_X_train = pd.read_csv('/home/c/cl237/TenBCD/UCI HAR/data/X_train.txt', delim_whitespace=True, header=None)
pd_X_train.columns = features
pd_y_train = pd.read_csv('/home/c/cl237/TenBCD/UCI HAR/data/y_train.txt', delim_whitespace=True, names=['Activity'])

N = len(pd_X_train)

K = 6

x = pd_X_train.values
y = pd_y_train.values

X_train=torch.tensor(x,dtype = torch.float64,device=device)
y_train=torch.tensor(y,dtype = int) #dtype=torch.int,device=device)

y_train = torch.flatten(y_train)

X_train = torch.t(X_train)

y_one_hot = torch.zeros(N, K).scatter_(1, torch.reshape(y_train-1, (N, 1)), 1)
y_one_hot = torch.t(y_one_hot).to(device=device)
y_train = y_train.to(device=device)

## get test data

In [5]:
pd_X_test = pd.read_csv('/home/c/cl237/TenBCD/UCI HAR/data/X_test.txt', delim_whitespace=True, header=None)
pd_X_test.columns = features
pd_y_test = pd.read_csv('/home/c/cl237/TenBCD/UCI HAR/data/y_test.txt', delim_whitespace=True, names=['Activity'])

N_test = len(pd_X_test)

x = pd_X_test.values
y = pd_y_test.values

X_test=torch.tensor(x,dtype = torch.float64, device=device)
y_test=torch.tensor(y,dtype = int)

y_test = torch.flatten(y_test)

X_test = torch.t(X_test)

y_test_one_hot = torch.zeros(N_test, K).scatter_(1, torch.reshape(y_test-1, (N_test, 1)), 1)
y_test_one_hot = torch.t(y_test_one_hot).to(device=device)
y_test = y_test.to(device=device)

# Main Algorithm

In [6]:
def updateV(U1,U2,W,b,rho,gamma): 
    _, d = W.size()
    I = torch.eye(d, device=device) #Returns a 2-D tensor with ones on the diagonal and zeros elsewhere.
    U1 = nn.ReLU()(U1)
    _, col_U2 = U2.size()
    Vstar = torch.mm(torch.inverse(rho*(torch.mm(torch.t(W),W))+gamma*I), rho*torch.mm(torch.t(W),U2-b.repeat(1,col_U2))+gamma*U1)
    return Vstar

def updateWb_org(U, V, W, b, alpha, rho): 
    d,N = V.size()
    I = torch.eye(d, device=device)
    _, col_U = U.size()
    Wstar = torch.mm(alpha*W+rho*torch.mm(U-b.repeat(1,col_U),torch.t(V)),torch.inverse(alpha*I+rho*(torch.mm(V,torch.t(V)))))
    bstar = 0*(alpha*b+rho*torch.sum(U-torch.mm(Wstar,V), dim=1).reshape(b.size()))/(rho*N+alpha)
    return Wstar, bstar

def updateWb(U, V, W, b, W_tensor_rec, alpha, rho,tau): 
    W_tensor_rec = torch.as_tensor(W_tensor_rec,device=device).float()
    W_tensor2matrix = W_tensor_rec.reshape(W.shape)
    d,N = V.size()
    I = torch.eye(d, device=device)
    _, col_U = U.size()
    Wstar = torch.mm(alpha*W+tau*W_tensor2matrix+rho*torch.mm(U-b.repeat(1,col_U),torch.t(V)),torch.inverse((alpha+tau)*I+rho*(torch.mm(V,torch.t(V)))))
    bstar = 0*(alpha*b+rho*torch.sum(U-torch.mm(Wstar,V), dim=1).reshape(b.size()))/(rho*N+alpha)
    return Wstar, bstar

# U update  E(1) in global convergent
def relu_prox(a, b, gamma, d, N):
    val = torch.empty(d,N, device=device)
    x = (a+gamma*b)/(1+gamma)
    y = torch.min(b,torch.zeros(d,N, device=device))

    val = torch.where(a+gamma*b < 0, y, torch.zeros(d,N, device=device))
    val = torch.where(((a+gamma*b >= 0) & (b >=0)) | ((a*(gamma-np.sqrt(gamma*(gamma+1))) <= gamma*b) & (b < 0)), x, val)
    val = torch.where((-a <= gamma*b) & (gamma*b <= a*(gamma-np.sqrt(gamma*(gamma+1)))), b, val)
    return val

# Model Initialization and training/testing

In [7]:
niter = 500
rank = 80
tau = 5
alpha = 1

for gamma in (0.01,0.1,0.5,1,5,10,100):
    for rho in (0.01,0.1,0.5,1,5,10,100): 
        
        print ("rank=",rank, "tau=",tau, "gamma=",gamma, "rho=",rho, "alpha",alpha)
        
        loss1 = np.empty(niter)
        loss2 = np.empty(niter)
        accuracy_train = np.empty(niter)
        accuracy_test = np.empty(niter)
        time1 = np.empty(niter)

        results = torch.zeros(1, 5, niter)



        for Out_iter in range(1):
            rank_initial = 400
            seed = 10 + 10*Out_iter
            torch.manual_seed(seed)
            if torch.cuda.is_available():
                torch.manual_seed(seed)
                
            d0 = 561 #561 =3*11*17
            d1 =  1024    # 2^10
            d2 =  1024  
            d3 = 1024
            d4 = 512      # 2^9
            d5 = 6 


            W1 = 0.01*torch.randn(d1, d0,dtype = torch.float64, device=device)
            W1_torch_tensor = W1.reshape((6,22,34,2,2,2,2,2,2,2))
            W1_tl_tensor = tl.tensor(W1_torch_tensor.cpu().numpy())
            factors1 = tensor_train(W1_tl_tensor, (1, rank_initial, rank_initial, rank_initial, rank_initial, rank_initial, rank_initial, rank_initial, rank_initial, rank_initial,1))
            W1_tl_tensor_rec = tt_to_tensor(factors1)
            b1 = 0*torch.ones(d1, 1, dtype = torch.float64,device=device) # 0 is stable


            W2 = 0.01*torch.randn(d2, d1, dtype = torch.float64,device=device)
            W2_torch_tensor = W2.reshape((4,4,4,4,4,4,4,4,4,4)) # 8 number of 4s, 2 number of 8s
            W2_tl_tensor = tl.tensor(W2_torch_tensor.cpu().numpy())
            factors2 = tensor_train(W2_tl_tensor, (1, rank_initial, rank_initial, rank_initial, rank_initial, rank_initial, rank_initial, rank_initial, rank_initial, rank_initial,1))
            W2_tl_tensor_rec = tt_to_tensor(factors2)    
            b2 = 0*torch.ones(d2, 1, dtype = torch.float64,device=device)


            W3 = 0.01*torch.randn(d3, d2, dtype = torch.float64,device=device)
            W3_torch_tensor = W3.reshape((4,4,4,4,4,4,4,4,4,4)) # 8 number of 4s, 2 number of 8s
            W3_tl_tensor = tl.tensor(W3_torch_tensor.cpu().numpy())
            factors3 = tensor_train(W3_tl_tensor, (1, rank_initial, rank_initial, rank_initial, rank_initial, rank_initial, rank_initial, rank_initial, rank_initial, rank_initial,1))
            W3_tl_tensor_rec = tt_to_tensor(factors3)
            b3 = 0*torch.ones(d3, 1, dtype = torch.float64,device=device)

            W4 = 0.01*torch.randn(d4, d3, dtype = torch.float64,device=device)
            W4_torch_tensor = W4.reshape((4,4,4,4,4,4,4,4,4,2)) # 8 number of 4s, 2 number of 8s
            W4_tl_tensor = tl.tensor(W4_torch_tensor.cpu().numpy())
            factors4 = tensor_train(W4_tl_tensor, (1, rank_initial, rank_initial, rank_initial, rank_initial, rank_initial, rank_initial, rank_initial, rank_initial, rank_initial,1))
            W4_tl_tensor_rec = tt_to_tensor(factors4)
            b4 = 0*torch.ones(d4, 1, dtype = torch.float64,device=device)


            W5 = 0.01*torch.randn(d5, d4, dtype = torch.float64,device=device)
            b5 = 0*torch.ones(d5, 1, dtype = torch.float64,device=device)



            U1 = torch.addmm(b1.repeat(1, N), W1, X_train)
            V1 = nn.ReLU()(U1)
            U2 = torch.addmm(b2.repeat(1, N), W2, V1)
            V2 = nn.ReLU()(U2)
            U3 = torch.addmm(b3.repeat(1, N), W3, V2)
            V3 = nn.ReLU()(U3)
            U4 = torch.addmm(b4.repeat(1, N), W4, V3)
            V4 = nn.ReLU()(U4)
            U5 = torch.addmm(b5.repeat(1, N), W5, V4)
            V5 = U5 




            # Iterations
            print('Train on', N, 'samples, validate on', N_test, 'samples')
            for k in range(niter):
                start = time.time()

         # update for last layer
                # update V4
                V5 = (y_one_hot + gamma*U5 + alpha*V5)/(1 + gamma + alpha)

                # update U4 
                U5 = (gamma*V5 + rho*(torch.mm(W5,V4) + b5.repeat(1,N)))/(gamma + rho)

                # update W4 and b4
                W5, b5 = updateWb_org(U5,V4,W5,b5,alpha,rho)



          # update for 4th layer
                # update V3
                V4 = updateV(U4,U5,W5,b5,rho,gamma)

                # update U3
                U4 = relu_prox(V4,(rho*torch.addmm(b4.repeat(1,N), W4, V3) + alpha*U4)/(rho + alpha),(rho + alpha)/gamma,d4,N)

                # update W3 and b3
                W4, b4 = updateWb(U4,V3,W4,b4,W4_tl_tensor_rec, alpha,rho,tau)

                # G update (TTD)   
                W4_torch_tensor = W4.reshape((4,4,4,4,4,4,4,4,4,2))
                W4_tl_tensor = tl.tensor(W4_torch_tensor.cpu().numpy())  # transfer tensorly package
                factors4 = tensor_train(W4_tl_tensor, (1,rank,rank,rank,rank,rank,rank,rank,rank,rank,1))
                #set of tensor cores
                W4_tl_tensor_rec = tt_to_tensor(factors4)

          # update for 3nd layer
                # update V3
                V3 = updateV(U3,U4,W4,b4,rho,gamma)

                # update U3
                U3 = relu_prox(V3,(rho*torch.addmm(b3.repeat(1,N), W3, V2) + alpha*U3)/(rho + alpha),(rho + alpha)/gamma,d3,N)

                # update W3 and b3
                W3, b3 = updateWb(U3,V2,W3,b3,W3_tl_tensor_rec, alpha,rho,tau)

                # G update (TTD)   
                W3_torch_tensor = W3.reshape((4,4,4,4,4,4,4,4,4,4))
                W3_tl_tensor = tl.tensor(W3_torch_tensor.cpu().numpy())  # transfer tensorly package
                factors3 = tensor_train(W3_tl_tensor, (1,rank,rank,rank,rank,rank,rank,rank,rank,rank,1))
                #set of tensor cores
                W3_tl_tensor_rec = tt_to_tensor(factors3)

         # update for 2nd layer
                # update V2
                V2 = updateV(U2,U3,W3,b3,rho,gamma)

                # update U2
                U2 = relu_prox(V2,(rho*torch.addmm(b2.repeat(1,N), W2, V1) + alpha*U2)/(rho + alpha),(rho + alpha)/gamma,d2,N)

                # update W2 and b2
                W2, b2 = updateWb(U2,V1,W2,b2,W2_tl_tensor_rec, alpha,rho,tau)

                # G update (TTD)   
                W2_torch_tensor = W2.reshape((4,4,4,4,4,4,4,4,4,4))
                W2_tl_tensor = tl.tensor(W2_torch_tensor.cpu().numpy()) 
                factors2 = tensor_train(W2_tl_tensor, (1,rank,rank,rank,rank,rank,rank,rank,rank,rank,1))
                W2_tl_tensor_rec = tt_to_tensor(factors2)


        # update for 1st layer
                # update V1
                V1 = updateV(U1,U2,W2,b2,rho,gamma)

                # update U1
                U1 = relu_prox(V1,(rho*torch.addmm(b1.repeat(1,N), W1, X_train) + alpha*U1)/(rho + alpha),(rho + alpha)/gamma,d1,N)

                # update W1 and b1
                W1, b1 = updateWb(U1,X_train,W1,b1,W1_tl_tensor_rec, alpha,rho,tau)

                # G update
                W1_torch_tensor = W1.reshape((6,22,34,2,2,2,2,2,2,2))
                W1_tl_tensor = tl.tensor(W1_torch_tensor.cpu().numpy())
                factors1 = tensor_train(W1_tl_tensor, (1,rank,rank,rank,rank,rank,rank,rank,rank,rank,1))
                W1_tl_tensor_rec = tt_to_tensor(factors1)




         # prediction for trainning data
                a1_train = nn.ReLU()(torch.addmm(b1.repeat(1, N), torch.as_tensor(W1_tl_tensor_rec,device=device).reshape((d1, d0)).double(), X_train))
                a2_train = nn.ReLU()(torch.addmm(b2.repeat(1, N), torch.as_tensor(W2_tl_tensor_rec,device=device).reshape((d2, d1)).double(), a1_train))
                a3_train = nn.ReLU()(torch.addmm(b3.repeat(1, N), torch.as_tensor(W3_tl_tensor_rec,device=device).reshape((d3, d2)).double(), a2_train))
                a4_train = nn.ReLU()(torch.addmm(b4.repeat(1, N), torch.as_tensor(W4_tl_tensor_rec,device=device).reshape((d4, d3)).double(), a3_train))
                pred = torch.argmax(torch.addmm(b5.repeat(1, N), W5, a4_train), dim=0)
                

         #Prediction for test data
                a1_test = nn.ReLU()(torch.addmm(b1.repeat(1, N_test), torch.as_tensor(W1_tl_tensor_rec,device=device).reshape((d1, d0)).double(), X_test))
                a2_test = nn.ReLU()(torch.addmm(b2.repeat(1, N_test), torch.as_tensor(W2_tl_tensor_rec,device=device).reshape((d2, d1)).double(), a1_test))
                a3_test = nn.ReLU()(torch.addmm(b3.repeat(1, N_test), torch.as_tensor(W3_tl_tensor_rec,device=device).reshape((d3, d2)).double(), a2_test))
                a4_test = nn.ReLU()(torch.addmm(b4.repeat(1, N_test), torch.as_tensor(W4_tl_tensor_rec,device=device).reshape((d4, d3)).double(), a3_test))
                pred_test = torch.argmax(torch.addmm(b5.repeat(1, N_test), W5, a4_test), dim=0)

                loss1[k] = gamma/2*torch.pow(torch.dist(V5,y_one_hot,2),2).cpu().numpy()

                loss2[k] = loss1[k] + rho/2*torch.pow(torch.dist(torch.addmm(b1.repeat(1,N), W1, X_train),U1,2),2).cpu().numpy() \
                +rho/2*torch.pow(torch.dist(torch.addmm(b2.repeat(1,N), W2, V1),U2,2),2).cpu().numpy() \
                +rho/2*torch.pow(torch.dist(torch.addmm(b3.repeat(1,N), W3, V2),U3,2),2).cpu().numpy() \
                +rho/2*torch.pow(torch.dist(torch.addmm(b4.repeat(1,N), W4, V3),U4,2),2).cpu().numpy() \
                +rho/2*torch.pow(torch.dist(torch.addmm(b5.repeat(1,N), W5, V4),U5,2),2).cpu().numpy() \
                + gamma/2*torch.pow(torch.dist(V1,nn.ReLU()(U1),2),2).cpu().numpy() \
                + gamma/2*torch.pow(torch.dist(V2,nn.ReLU()(U2),2),2).cpu().numpy() \
                + gamma/2*torch.pow(torch.dist(V3,nn.ReLU()(U3),2),2).cpu().numpy() \
                + gamma/2*torch.pow(torch.dist(V4,nn.ReLU()(U4),2),2).cpu().numpy() \
                + gamma/2*torch.pow(torch.dist(V5,U5,2),2).cpu().numpy() \
                +tau/2*torch.pow(torch.dist(W1.reshape((6,22,34,2,2,2,2,2,2,2)),torch.as_tensor(W1_tl_tensor_rec,device=device).float(),2),2).cpu().numpy() \
                +tau/2*torch.pow(torch.dist(W2.reshape((4,4,4,4,4,4,4,4,4,4)),torch.as_tensor(W2_tl_tensor_rec,device=device).float(),2),2).cpu().numpy() \
                +tau/2*torch.pow(torch.dist(W3.reshape((4,4,4,4,4,4,4,4,4,4)),torch.as_tensor(W3_tl_tensor_rec,device=device).float(),2),2).cpu().numpy() \
                +tau/2*torch.pow(torch.dist(W4.reshape((4,4,4,4,4,4,4,4,4,2)),torch.as_tensor(W4_tl_tensor_rec,device=device).float(),2),2).cpu().numpy() \


                # compute training accuracy
                correct_train = pred == y_train-1
                accuracy_train[k] = np.mean(correct_train.cpu().numpy())

                # compute validation accuracy
                correct_test = pred_test == y_test-1
                accuracy_test[k] = np.mean(correct_test.cpu().numpy())

                # compute training time
                stop = time.time()
                duration = stop - start
                time1[k] = duration

                # print results
                print('Repeatition', Out_iter + 1, 'Epoch', k + 1, '/', niter, '\n', 
                      '-', 'time:', time1[k], '-', 'sq_loss:', loss1[k], '-', 'tot_loss:', loss2[k], 
                      '-', 'acc:', accuracy_train[k], '-', 'val_acc:', accuracy_test[k])

        ##############
        ############## compute CR
            factors1_shape=[f.shape for f in factors1]
            Sum_of_variables_factors1=sum(list(x*y*z for x,y,z in factors1_shape))
            factors2_shape=[f.shape for f in factors2]
            Sum_of_variables_factors2=sum(list(x*y*z for x,y,z in factors2_shape))
            factors3_shape=[f.shape for f in factors3]
            Sum_of_variables_factors3=sum(list(x*y*z for x,y,z in factors3_shape))
            factors4_shape=[f.shape for f in factors4]
            Sum_of_variables_factors4=sum(list(x*y*z for x,y,z in factors4_shape))

            total_variabels=Sum_of_variables_factors1+Sum_of_variables_factors2+Sum_of_variables_factors3+Sum_of_variables_factors4

            CR_1=((total_variabels)+(d4*d5))/(d0*d1+d1*d2+d2*d3+d3*d4+d4*d5)
            CR_2=(total_variabels)/(d0*d1+d1*d2+d2*d3+d3*d4)
            print("CR_1 = "+str(CR_1)+"   "+"CR_2 = " +str(CR_2))


            results[Out_iter,0,:] = torch.tensor(loss1)
            results[Out_iter,1,:] = torch.tensor(loss2)
            results[Out_iter,2,:] = torch.tensor(accuracy_train)
            results[Out_iter,3,:] = torch.tensor(accuracy_test)
            results[Out_iter,4,:] = torch.tensor(time1)
            CR=(CR_1,CR_2)


rank= 80 tau= 5 gamma= 0.01 rho= 0.01 alpha 1
Train on 7352 samples, validate on 2947 samples
Repeatition 1 Epoch 1 / 500 
 - time: 1.7410342693328857 - sq_loss: 9.284291996489848 - tot_loss: 551.0934160675939 - acc: 0.19980957562568008 - val_acc: 0.19273837801153715
Repeatition 1 Epoch 2 / 500 
 - time: 1.4566214084625244 - sq_loss: 2.367262374558384 - tot_loss: 37.488806126867196 - acc: 0.1913764961915125 - val_acc: 0.18221920597217509
Repeatition 1 Epoch 3 / 500 
 - time: 1.4851901531219482 - sq_loss: 0.6148688811703954 - tot_loss: 20.46421288157004 - acc: 0.1913764961915125 - val_acc: 0.18221920597217509
Repeatition 1 Epoch 4 / 500 
 - time: 1.4648659229278564 - sq_loss: 0.16472091520538595 - tot_loss: 16.374488562161815 - acc: 0.1913764961915125 - val_acc: 0.18221920597217509
Repeatition 1 Epoch 5 / 500 
 - time: 1.4674994945526123 - sq_loss: 0.0458061980922759 - tot_loss: 13.495271873318947 - acc: 0.1913764961915125 - val_acc: 0.18221920597217509
Repeatition 1 Epoch 6 / 500 
 - t